In [1]:
from google.colab import drive
drive.mount('/root/gdrive')


Mounted at /root/gdrive


In [2]:
!pip install transformers
!pip install tqdm
!pip install nltk
!pip install sentence-transformers


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 35.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 28.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 97.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 63.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 1.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 24.3 MB/s eta 0:00:00
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125925 sha256=3ad6761d1b701e817bb41229acc4110ad0824cdbb2ca4773ce67b98d41f8f67c
  Stored in directory: /root/.cache/pip/wheels/62/f2/10/1e606fd5f02395388f74e7462910fe851042f97238cbbd902f
Successfully built sentence-transformers


In [3]:
import nltk
nltk.download('wordnet')
nltk.download('stopwords')

import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics import accuracy_score

import numpy as np

import re
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from tqdm import tqdm
import torch



[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [4]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')


In [5]:
pip install openprompt


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 146.4/146.4 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.6/101.6 kB 11.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.1/519.1 kB 11.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 16.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 14.2 MB/s eta 0:00:00
  Attempting uninstall: sentencepiece
    Found existing installation: sentencepiece 0.1.99
    Uninstalling sentencepiece-0.1.99:
      Successfully uninstalled sentencepiece-0.1.99


In [6]:
cd /root/gdrive/MyDrive/OpenPrompt

/root/gdrive/MyDrive/OpenPrompt


In [7]:
pip install -r requirements.txt

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.2/244.2 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.1/731.1 kB 8.3 MB/s eta 0:00:00


In [8]:
from openprompt.data_utils.text_classification_dataset import AgnewsProcessor  # load specific news processor
from openprompt.data_utils.data_sampler import FewShotSampler # few shot
from openprompt.plms import load_plm
from openprompt.prompts import ManualTemplate
from openprompt.prompts import ManualVerbalizer
from openprompt import PromptDataLoader
from openprompt.prompts import SoftVerbalizer
from openprompt import PromptForClassification
import torch
from transformers import  AdamW, get_linear_schedule_with_warmup
from sklearn.metrics import accuracy_score
from openprompt.data_utils.text_classification_dataset import ToxicityProcessor


/usr/local/lib/python3.10/dist-packages/transformers/generation_utils.py:24: FutureWarning: Importing `GenerationMixin` from `src/transformers/generation_utils.py` is deprecated and will be removed in Transformers v5. Import as `from transformers import GenerationMixin` instead.
  warnings.warn(


In [9]:
dataset = {}
# trainvalid_dataset = processor.get_train_examples(dataset_path)
dataset['train'] = ToxicityProcessor().get_train_examples("/root/gdrive/MyDrive/toxicity_data")
#sampler  = FewShotSampler(num_examples_per_label=3, num_examples_per_label_dev=3, also_sample_dev=True)
#dataset['train'], dataset['validation'] = sampler(dataset['train'])
dataset['test'] = ToxicityProcessor().get_test_examples("/root/gdrive/MyDrive/toxicity_data")
print(len(dataset['train']))
print(len(dataset['test']))
print(dataset['train'][0])


51182
12796
{
  "guid": "83aa72a87f749fdc",
  "label": 1,
  "meta": {},
  "text_a": "lennie injured remainder season gettin prono three fucked brown crooked cant get game alnwick never get game spur fucked lawrence club going ahhahahahah fuck porno three hate scum hope mother saw knocking bint bunch filthy pikey bastard",
  "text_b": "",
  "tgt_text": null
}



In [10]:
classes = ['0','1']


In [11]:
#plm, tokenizer, model_config, WrapperClass=load_plm("bert", "bert-base-cased") # load pretrained model
#plm, tokenizer, model_config, WrapperClass = load_plm("t5", "t5-base")
plm, tokenizer, model_config, WrapperClass=load_plm("opt", "facebook/opt-1.3b")


In [13]:
# define the template
#template = ManualTemplate(tokenizer=tokenizer, text= '{"placeholder":"text_a"} It was {"mask"}',)
#template = ManualTemplate(tokenizer=tokenizer, text= 'What is the toxicity label of {"placeholder":"text_a"}? It was {"mask"}',)
#template = ManualTemplate(tokenizer=tokenizer, text= 'Analyzing the comment {"placeholder":"text_a"}, it can be determined that the toxicity label is {"mask"}',)
verbalizer = ManualVerbalizer(
    classes = classes,
    label_words = {
        #"0": ['non-toxic'],
        #"0": ['non-toxic', 'harmless', 'wholesome', 'decent','comforting', 'respectful', 'nondiscriminatory'],
        #"1": ['toxic', 'harmful', 'noxious', 'indecent', 'menacing', 'impertinent', 'discriminatory'],
        "0": ['acceptable', 'respectful', 'civil', 'polite'],
        "1": ['offensive', 'rude', 'disrespectful', 'vulgar'],
    },
    tokenizer = tokenizer,
)

#verbalizer = SoftVerbalizer(tokenizer, plm, num_classes=2)

#wrapped_example = template.wrap_one_example(dataset['train'][0])
#print('wrapped_example:',wrapped_example)


In [14]:
use_cuda = True
# build the prompt model
prompt_model = PromptForClassification(plm=plm,template=None, verbalizer=verbalizer, freeze_plm=False)
if use_cuda:
    prompt_model = prompt_model.cuda()


In [15]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity

# Load SentenceTransformer model
model = SentenceTransformer('all-MiniLM-L6-v2')

# Get sentence embeddings
train_sentences = [ex.text_a for ex in dataset['train']]
train_embeddings = model.encode(train_sentences)

test_sentences = [ex.text_a for ex in dataset['test']]
test_embeddings = model.encode(test_sentences)


In [16]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report
from sklearn.neighbors import KDTree


In [17]:
tree = KDTree(train_embeddings)


In [17]:
#"0": ['non-toxic']
#"1": ['toxic', 'harmful', 'noxious', 'indecent', 'menacing', 'impertinent', 'discriminatory']

# For predictions and true labels
allpreds = []
alllabels = []

top_k = 4
use_cuda = torch.cuda.is_available()
device = torch.device('cuda' if use_cuda else 'cpu')

# Build the prompt model
prompt_model = PromptForClassification(plm=plm, template=None, verbalizer=verbalizer, freeze_plm=False)
if use_cuda:
    prompt_model = prompt_model.cuda()

max_seq_length = 2048

for idx, test_example in enumerate(tqdm(dataset['test'], desc="Predicting", unit="batch")):
    test_sentence = test_example.text_a
    test_embedding = model.encode([test_sentence])[0]  # Get the embedding of the test_sentence

    # calculate the cosine similarity between the test sentence embedding and all train sentence embeddings
    #similarities = cosine_similarity([test_embedding], train_embeddings)[0]

    # find the top k most similar train sentences
    #top_k_indices = similarities.argsort()[-top_k:]
    #top_k_train_examples = [dataset['train'][i] for i in top_k_indices]

    # find the top k most similar train sentences
    _, top_k_indices = tree.query([test_embedding], k=top_k)
    top_k_train_examples = [dataset['train'][i] for i in top_k_indices[0]]


    # Truncate top_k_train_examples and create template
    few_shot_text = ""
    for ex in top_k_train_examples:
        temp_text = f"{ex.text_a} It was {verbalizer.label_words[ex.label][0]}."
        temp_text = temp_text if len(temp_text) <= 1600 else temp_text[:1597] + "..."
        few_shot_text += temp_text

    template = ManualTemplate(tokenizer=tokenizer, text=f'{few_shot_text} {{ "placeholder":"text_a" }} It was {{ "mask" }}')

    # Check if the total tokens after tokenization would exceed max_seq_length
    total_tokens = len(tokenizer.tokenize(few_shot_text)) + len(tokenizer.tokenize(test_sentence))
    if total_tokens > max_seq_length:
        print(f'Skipping example {idx} as the total token count {total_tokens} exceeds the maximum sequence length {max_seq_length}.')
        continue

    prompt_model = PromptForClassification(plm=plm, template=template, verbalizer=verbalizer, freeze_plm=False)
    test_dataloader = PromptDataLoader(dataset=[test_example], template=template, tokenizer=tokenizer, tokenizer_wrapper_class=WrapperClass, max_seq_length=2048, batch_size=16, teacher_forcing=False, predict_eos_token=False, truncate_method='tail')

    with torch.no_grad():
        for inputs in test_dataloader:
            if use_cuda:
                inputs = {k: v.to(device) for k, v in inputs.items() if torch.is_tensor(v)}
            logits = prompt_model(inputs)
            labels = inputs['label']
            preds = torch.argmax(logits, dim=-1)
            allpreds.append(preds[0])
            alllabels.append(labels[0])

# Once all predictions are done, move lists to CPU
allpreds = [pred.item() for pred in allpreds]
alllabels = [label.item() for label in alllabels]

# Compute accuracy
accuracy = accuracy_score(alllabels, allpreds)
precision = precision_score(alllabels, allpreds, average='weighted')  # Considering class imbalance
recall = recall_score(alllabels, allpreds, average='weighted')  # Considering class imbalance
f1 = f1_score(alllabels, allpreds, average='weighted')  # Considering class imbalance

print('Accuracy:', accuracy)
print('Precision:', precision)
print('Recall:', recall)
print('F1 Score:', f1)

# Print classification report
report = classification_report(alllabels, allpreds)
print('Classification Report:')
print(report)

Predicting:   0%|          | 0/12796 [00:00<?, ?batch/s]
tokenizing: 1it [00:00, 87.75it/s]
Predicting:   0%|          | 1/12796 [00:00<2:26:52,  1.45batch/s]
tokenizing: 1it [00:00, 183.92it/s]
Predicting:   0%|          | 2/12796 [00:01<2:22:35,  1.50batch/s]
tokenizing: 1it [00:00, 137.69it/s]
Predicting:   0%|          | 3/12796 [00:01<2:21:14,  1.51batch/s]
tokenizing: 1it [00:00, 226.35it/s]
Predicting:   0%|          | 4/12796 [00:02<2:19:48,  1.53batch/s]
tokenizing: 1it [00:00, 117.72it/s]
Predicting:   0%|          | 5/12796 [00:03<2:20:21,  1.52batch/s]
tokenizing: 1it [00:00, 232.63it/s]
Predicting:   0%|          | 6/12796 [00:03<2:19:46,  1.53batch/s]
tokenizing: 1it [00:00, 176.64it/s]
Predicting:   0%|          | 7/12796 [00:04<2:19:39,  1.53batch/s]
tokenizing: 1it [00:00, 181.19it/s]
Predicting:   0%|          | 8/12796 [00:05<2:19:21,  1.53batch/s]
tokenizing: 1it [00:00, 88.17it/s]
Predicting:   0%|          | 9/12796 [00:05<2:22:01,  1.50batch/s]
tokenizing: 1it [0

Skipping example 79 as the total token count 2481 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 255.63it/s]
Predicting:   1%|          | 81/12796 [00:55<1:49:57,  1.93batch/s]
tokenizing: 1it [00:00, 115.36it/s]
Predicting:   1%|          | 82/12796 [00:56<1:58:48,  1.78batch/s]
tokenizing: 1it [00:00, 150.54it/s]
Predicting:   1%|          | 83/12796 [00:57<2:05:07,  1.69batch/s]
tokenizing: 1it [00:00, 132.68it/s]
Predicting:   1%|          | 84/12796 [00:57<2:09:51,  1.63batch/s]
tokenizing: 1it [00:00, 62.70it/s]
Predicting:   1%|          | 85/12796 [00:58<2:15:28,  1.56batch/s]
tokenizing: 1it [00:00, 180.90it/s]
Predicting:   1%|          | 86/12796 [00:59<2:17:34,  1.54batch/s]
tokenizing: 1it [00:00, 68.68it/s]
Predicting:   1%|          | 87/12796 [00:59<2:20:18,  1.51batch/s]
tokenizing: 1it [00:00, 114.46it/s]
Predicting:   1%|          | 88/12796 [01:00<2:21:24,  1.50batch/s]
tokenizing: 1it [00:00, 126.42it/s]
Predicting:   1%|          | 89/12796 [01:01<2:22:35,  1.49batch/s]
tokenizing: 1it [00:00, 130.12it/s]
Predicting:   1%|          | 

Skipping example 96 as the total token count 4606 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 114.06it/s]
Predicting:   1%|          | 98/12796 [01:06<1:51:23,  1.90batch/s]
tokenizing: 1it [00:00, 102.98it/s]
Predicting:   1%|          | 99/12796 [01:07<1:58:29,  1.79batch/s]
tokenizing: 1it [00:00, 163.50it/s]
Predicting:   1%|          | 100/12796 [01:07<2:04:00,  1.71batch/s]
tokenizing: 1it [00:00, 139.34it/s]
Predicting:   1%|          | 101/12796 [01:08<2:08:13,  1.65batch/s]
tokenizing: 1it [00:00, 193.33it/s]
Predicting:   1%|          | 102/12796 [01:09<2:10:59,  1.62batch/s]
tokenizing: 1it [00:00, 197.78it/s]
Predicting:   1%|          | 103/12796 [01:09<2:13:22,  1.59batch/s]
tokenizing: 1it [00:00, 123.20it/s]
Predicting:   1%|          | 104/12796 [01:10<2:14:51,  1.57batch/s]
tokenizing: 1it [00:00, 257.46it/s]
Predicting:   1%|          | 105/12796 [01:11<2:15:46,  1.56batch/s]
tokenizing: 1it [00:00, 334.53it/s]
Predicting:   1%|          | 106/12796 [01:11<2:16:52,  1.55batch/s]
tokenizing: 1it [00:00, 148.90it/s]
Predicting:   1%|   

...


tokenizing: 1it [00:00, 150.93it/s]
Predicting:  99%|█████████▉| 12674/12796 [2:21:40<01:05,  1.86batch/s]
tokenizing: 1it [00:00, 199.70it/s]
Predicting:  99%|█████████▉| 12675/12796 [2:21:41<01:09,  1.75batch/s]
tokenizing: 1it [00:00, 113.06it/s]
Predicting:  99%|█████████▉| 12676/12796 [2:21:42<01:11,  1.68batch/s]
tokenizing: 1it [00:00, 164.92it/s]
Predicting:  99%|█████████▉| 12677/12796 [2:21:42<01:13,  1.63batch/s]
tokenizing: 1it [00:00, 201.09it/s]
Predicting:  99%|█████████▉| 12678/12796 [2:21:43<01:14,  1.59batch/s]
tokenizing: 1it [00:00, 181.74it/s]
Predicting:  99%|█████████▉| 12679/12796 [2:21:44<01:14,  1.57batch/s]
tokenizing: 1it [00:00, 154.62it/s]
Predicting:  99%|█████████▉| 12680/12796 [2:21:44<01:14,  1.55batch/s]
tokenizing: 1it [00:00, 105.77it/s]
Predicting:  99%|█████████▉| 12681/12796 [2:21:45<01:14,  1.54batch/s]
tokenizing: 1it [00:00, 72.61it/s]
Predicting:  99%|█████████▉| 12682/12796 [2:21:46<01:16,  1.50batch/s]
tokenizing: 1it [00:00, 268.13it/s]
P

Skipping example 12754 as the total token count 6850 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 192.80it/s]
Predicting: 100%|█████████▉| 12756/12796 [2:22:35<00:21,  1.89batch/s]
tokenizing: 1it [00:00, 199.06it/s]
Predicting: 100%|█████████▉| 12757/12796 [2:22:36<00:22,  1.77batch/s]
tokenizing: 1it [00:00, 243.85it/s]
Predicting: 100%|█████████▉| 12758/12796 [2:22:36<00:22,  1.70batch/s]
tokenizing: 1it [00:00, 129.56it/s]
Predicting: 100%|█████████▉| 12759/12796 [2:22:37<00:22,  1.64batch/s]
tokenizing: 1it [00:00, 173.17it/s]
Predicting: 100%|█████████▉| 12760/12796 [2:22:38<00:22,  1.60batch/s]
tokenizing: 1it [00:00, 225.66it/s]
Predicting: 100%|█████████▉| 12761/12796 [2:22:38<00:22,  1.57batch/s]
tokenizing: 1it [00:00, 154.47it/s]
Predicting: 100%|█████████▉| 12762/12796 [2:22:39<00:21,  1.56batch/s]
tokenizing: 1it [00:00, 86.95it/s]
Predicting: 100%|█████████▉| 12763/12796 [2:22:40<00:21,  1.53batch/s]
tokenizing: 1it [00:00, 149.12it/s]
Predicting: 100%|█████████▉| 12764/12796 [2:22:40<00:21,  1.51batch/s]
tokenizing: 1it [00:00, 127.90it/s]
P

Accuracy: 0.9025443694047433
Precision: 0.8145863387442056
Recall: 0.9025443694047433
F1 Score: 0.8563125799784302
Classification Report:
              precision    recall  f1-score   support

           0       0.90      1.00      0.95     11493
           1       0.00      0.00      0.00      1241

    accuracy                           0.90     12734
   macro avg       0.45      0.50      0.47     12734
weighted avg       0.81      0.90      0.86     12734



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:13

In [23]:
#"0": ['non-toxic', 'harmless', 'wholesome', 'decent','comforting', 'respectful', 'nondiscriminatory'],
#"1": ['toxic', 'harmful', 'noxious', 'indecent', 'menacing', 'impertinent', 'discriminatory'],

# For predictions and true labels
allpreds = []
alllabels = []

top_k = 4
use_cuda = torch.cuda.is_available()
device = torch.device('cuda' if use_cuda else 'cpu')

# Build the prompt model
prompt_model = PromptForClassification(plm=plm, template=None, verbalizer=verbalizer, freeze_plm=False)
if use_cuda:
    prompt_model = prompt_model.cuda()

max_seq_length = 2048

for idx, test_example in enumerate(tqdm(dataset['test'], desc="Predicting", unit="batch")):
    test_sentence = test_example.text_a
    test_embedding = model.encode([test_sentence])[0]  # Get the embedding of the test_sentence

    # calculate the cosine similarity between the test sentence embedding and all train sentence embeddings
    #similarities = cosine_similarity([test_embedding], train_embeddings)[0]

    # find the top k most similar train sentences
    #top_k_indices = similarities.argsort()[-top_k:]
    #top_k_train_examples = [dataset['train'][i] for i in top_k_indices]

    # find the top k most similar train sentences
    _, top_k_indices = tree.query([test_embedding], k=top_k)
    top_k_train_examples = [dataset['train'][i] for i in top_k_indices[0]]


    # Truncate top_k_train_examples and create template
    few_shot_text = ""
    for ex in top_k_train_examples:
        temp_text = f"{ex.text_a} It was {verbalizer.label_words[ex.label][0]}."
        temp_text = temp_text if len(temp_text) <= 1600 else temp_text[:1597] + "..."
        few_shot_text += temp_text

    template = ManualTemplate(tokenizer=tokenizer, text=f'{few_shot_text} {{ "placeholder":"text_a" }} It was {{ "mask" }}')

    # Check if the total tokens after tokenization would exceed max_seq_length
    total_tokens = len(tokenizer.tokenize(few_shot_text)) + len(tokenizer.tokenize(test_sentence))
    if total_tokens > max_seq_length:
        print(f'Skipping example {idx} as the total token count {total_tokens} exceeds the maximum sequence length {max_seq_length}.')
        continue

    prompt_model = PromptForClassification(plm=plm, template=template, verbalizer=verbalizer, freeze_plm=False)
    test_dataloader = PromptDataLoader(dataset=[test_example], template=template, tokenizer=tokenizer, tokenizer_wrapper_class=WrapperClass, max_seq_length=2048, batch_size=16, teacher_forcing=False, predict_eos_token=False, truncate_method='tail')

    with torch.no_grad():
        for inputs in test_dataloader:
            if use_cuda:
                inputs = {k: v.to(device) for k, v in inputs.items() if torch.is_tensor(v)}
            logits = prompt_model(inputs)
            labels = inputs['label']
            preds = torch.argmax(logits, dim=-1)
            allpreds.append(preds[0])
            alllabels.append(labels[0])

# Once all predictions are done, move lists to CPU
allpreds = [pred.item() for pred in allpreds]
alllabels = [label.item() for label in alllabels]

# Compute accuracy
accuracy = accuracy_score(alllabels, allpreds)
precision = precision_score(alllabels, allpreds, average='weighted')  # Considering class imbalance
recall = recall_score(alllabels, allpreds, average='weighted')  # Considering class imbalance
f1 = f1_score(alllabels, allpreds, average='weighted')  # Considering class imbalance

print('Accuracy:', accuracy)
print('Precision:', precision)
print('Recall:', recall)
print('F1 Score:', f1)

# Print classification report
report = classification_report(alllabels, allpreds)
print('Classification Report:')
print(report)

Predicting:   0%|          | 0/12796 [00:00<?, ?batch/s]
tokenizing: 1it [00:00, 79.59it/s]
Predicting:   0%|          | 1/12796 [00:00<2:21:24,  1.51batch/s]
tokenizing: 1it [00:00, 434.33it/s]
Predicting:   0%|          | 2/12796 [00:01<2:20:09,  1.52batch/s]
tokenizing: 1it [00:00, 348.25it/s]
Predicting:   0%|          | 3/12796 [00:01<2:19:30,  1.53batch/s]
tokenizing: 1it [00:00, 303.58it/s]
Predicting:   0%|          | 4/12796 [00:02<2:19:01,  1.53batch/s]
tokenizing: 1it [00:00, 88.68it/s]
Predicting:   0%|          | 5/12796 [00:03<2:19:59,  1.52batch/s]
tokenizing: 1it [00:00, 243.20it/s]
Predicting:   0%|          | 6/12796 [00:03<2:19:49,  1.52batch/s]
tokenizing: 1it [00:00, 258.46it/s]
Predicting:   0%|          | 7/12796 [00:04<2:19:16,  1.53batch/s]
tokenizing: 1it [00:00, 153.60it/s]
Predicting:   0%|          | 8/12796 [00:05<2:20:10,  1.52batch/s]
tokenizing: 1it [00:00, 113.02it/s]
Predicting:   0%|          | 9/12796 [00:05<2:21:29,  1.51batch/s]
tokenizing: 1it [0

Skipping example 79 as the total token count 2481 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 205.66it/s]
Predicting:   1%|          | 81/12796 [00:53<1:58:01,  1.80batch/s]
tokenizing: 1it [00:00, 232.26it/s]
Predicting:   1%|          | 82/12796 [00:54<2:03:11,  1.72batch/s]
tokenizing: 1it [00:00, 194.25it/s]
Predicting:   1%|          | 83/12796 [00:55<2:08:32,  1.65batch/s]
tokenizing: 1it [00:00, 145.64it/s]
Predicting:   1%|          | 84/12796 [00:55<2:12:11,  1.60batch/s]
tokenizing: 1it [00:00, 79.63it/s]
Predicting:   1%|          | 85/12796 [00:56<2:15:54,  1.56batch/s]
tokenizing: 1it [00:00, 218.69it/s]
Predicting:   1%|          | 86/12796 [00:57<2:17:32,  1.54batch/s]
tokenizing: 1it [00:00, 98.33it/s]
Predicting:   1%|          | 87/12796 [00:57<2:19:33,  1.52batch/s]
tokenizing: 1it [00:00, 114.10it/s]
Predicting:   1%|          | 88/12796 [00:58<2:20:55,  1.50batch/s]
tokenizing: 1it [00:00, 125.44it/s]
Predicting:   1%|          | 89/12796 [00:59<2:22:45,  1.48batch/s]
tokenizing: 1it [00:00, 122.42it/s]
Predicting:   1%|          | 

Skipping example 96 as the total token count 4606 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 126.96it/s]
Predicting:   1%|          | 98/12796 [01:04<1:51:25,  1.90batch/s]
tokenizing: 1it [00:00, 87.10it/s]
Predicting:   1%|          | 99/12796 [01:05<1:58:33,  1.79batch/s]
tokenizing: 1it [00:00, 165.12it/s]
Predicting:   1%|          | 100/12796 [01:05<2:04:02,  1.71batch/s]
tokenizing: 1it [00:00, 173.08it/s]
Predicting:   1%|          | 101/12796 [01:06<2:07:58,  1.65batch/s]
tokenizing: 1it [00:00, 317.92it/s]
Predicting:   1%|          | 102/12796 [01:07<2:10:53,  1.62batch/s]
tokenizing: 1it [00:00, 140.81it/s]
Predicting:   1%|          | 103/12796 [01:07<2:13:17,  1.59batch/s]
tokenizing: 1it [00:00, 149.34it/s]
Predicting:   1%|          | 104/12796 [01:08<2:15:13,  1.56batch/s]
tokenizing: 1it [00:00, 224.07it/s]
Predicting:   1%|          | 105/12796 [01:09<2:16:11,  1.55batch/s]
tokenizing: 1it [00:00, 148.09it/s]
Predicting:   1%|          | 106/12796 [01:09<2:16:47,  1.55batch/s]
tokenizing: 1it [00:00, 183.90it/s]
Predicting:   1%|    

...

Skipping example 12672 as the total token count 3090 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 89.51it/s]
Predicting:  99%|█████████▉| 12674/12796 [2:21:41<01:08,  1.77batch/s]
tokenizing: 1it [00:00, 193.15it/s]
Predicting:  99%|█████████▉| 12675/12796 [2:21:41<01:12,  1.67batch/s]
tokenizing: 1it [00:00, 117.18it/s]
Predicting:  99%|█████████▉| 12676/12796 [2:21:42<01:15,  1.60batch/s]
tokenizing: 1it [00:00, 119.76it/s]
Predicting:  99%|█████████▉| 12677/12796 [2:21:43<01:16,  1.55batch/s]
tokenizing: 1it [00:00, 127.23it/s]
Predicting:  99%|█████████▉| 12678/12796 [2:21:43<01:17,  1.52batch/s]
tokenizing: 1it [00:00, 163.56it/s]
Predicting:  99%|█████████▉| 12679/12796 [2:21:44<01:17,  1.50batch/s]
tokenizing: 1it [00:00, 160.43it/s]
Predicting:  99%|█████████▉| 12680/12796 [2:21:45<01:18,  1.49batch/s]
tokenizing: 1it [00:00, 124.47it/s]
Predicting:  99%|█████████▉| 12681/12796 [2:21:45<01:17,  1.47batch/s]
tokenizing: 1it [00:00, 77.23it/s]
Predicting:  99%|█████████▉| 12682/12796 [2:21:46<01:18,  1.45batch/s]
tokenizing: 1it [00:00, 288.17it/s]
Pr

Skipping example 12754 as the total token count 6850 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 95.28it/s]
Predicting: 100%|█████████▉| 12756/12796 [2:22:35<00:22,  1.77batch/s]
tokenizing: 1it [00:00, 120.14it/s]
Predicting: 100%|█████████▉| 12757/12796 [2:22:36<00:23,  1.67batch/s]
tokenizing: 1it [00:00, 259.15it/s]
Predicting: 100%|█████████▉| 12758/12796 [2:22:37<00:23,  1.61batch/s]
tokenizing: 1it [00:00, 70.60it/s]
Predicting: 100%|█████████▉| 12759/12796 [2:22:37<00:23,  1.55batch/s]
tokenizing: 1it [00:00, 225.44it/s]
Predicting: 100%|█████████▉| 12760/12796 [2:22:38<00:23,  1.53batch/s]
tokenizing: 1it [00:00, 109.77it/s]
Predicting: 100%|█████████▉| 12761/12796 [2:22:39<00:23,  1.51batch/s]
tokenizing: 1it [00:00, 113.62it/s]
Predicting: 100%|█████████▉| 12762/12796 [2:22:40<00:22,  1.48batch/s]
tokenizing: 1it [00:00, 131.98it/s]
Predicting: 100%|█████████▉| 12763/12796 [2:22:40<00:22,  1.48batch/s]
tokenizing: 1it [00:00, 128.17it/s]
Predicting: 100%|█████████▉| 12764/12796 [2:22:41<00:21,  1.48batch/s]
tokenizing: 1it [00:00, 127.96it/s]
Pr

Accuracy: 0.8479660750746034
Precision: 0.8920530207883878
Recall: 0.8479660750746034
F1 Score: 0.8653029619925832
Classification Report:
              precision    recall  f1-score   support

           0       0.95      0.88      0.91     11493
           1       0.34      0.59      0.43      1241

    accuracy                           0.85     12734
   macro avg       0.65      0.73      0.67     12734
weighted avg       0.89      0.85      0.87     12734



In [18]:
#"0": ['acceptable', 'respectful', 'civil', 'polite'],
#"1": ['offensive', 'rude', 'disrespectful', 'vulgar'],

# For predictions and true labels
allpreds = []
alllabels = []

top_k = 4
use_cuda = torch.cuda.is_available()
device = torch.device('cuda' if use_cuda else 'cpu')

# Build the prompt model
prompt_model = PromptForClassification(plm=plm, template=None, verbalizer=verbalizer, freeze_plm=False)
if use_cuda:
    prompt_model = prompt_model.cuda()

max_seq_length = 2048

for idx, test_example in enumerate(tqdm(dataset['test'], desc="Predicting", unit="batch")):
    test_sentence = test_example.text_a
    test_embedding = model.encode([test_sentence])[0]  # Get the embedding of the test_sentence

    # calculate the cosine similarity between the test sentence embedding and all train sentence embeddings
    #similarities = cosine_similarity([test_embedding], train_embeddings)[0]

    # find the top k most similar train sentences
    #top_k_indices = similarities.argsort()[-top_k:]
    #top_k_train_examples = [dataset['train'][i] for i in top_k_indices]

    # find the top k most similar train sentences
    _, top_k_indices = tree.query([test_embedding], k=top_k)
    top_k_train_examples = [dataset['train'][i] for i in top_k_indices[0]]


    # Truncate top_k_train_examples and create template
    few_shot_text = ""
    for ex in top_k_train_examples:
        temp_text = f"{ex.text_a} It was {verbalizer.label_words[ex.label][0]}."
        temp_text = temp_text if len(temp_text) <= 1600 else temp_text[:1597] + "..."
        few_shot_text += temp_text

    template = ManualTemplate(tokenizer=tokenizer, text=f'{few_shot_text} {{ "placeholder":"text_a" }} It was {{ "mask" }}')

    # Check if the total tokens after tokenization would exceed max_seq_length
    total_tokens = len(tokenizer.tokenize(few_shot_text)) + len(tokenizer.tokenize(test_sentence))
    if total_tokens > max_seq_length:
        print(f'Skipping example {idx} as the total token count {total_tokens} exceeds the maximum sequence length {max_seq_length}.')
        continue

    prompt_model = PromptForClassification(plm=plm, template=template, verbalizer=verbalizer, freeze_plm=False)
    test_dataloader = PromptDataLoader(dataset=[test_example], template=template, tokenizer=tokenizer, tokenizer_wrapper_class=WrapperClass, max_seq_length=2048, batch_size=16, teacher_forcing=False, predict_eos_token=False, truncate_method='tail')

    with torch.no_grad():
        for inputs in test_dataloader:
            if use_cuda:
                inputs = {k: v.to(device) for k, v in inputs.items() if torch.is_tensor(v)}
            logits = prompt_model(inputs)
            labels = inputs['label']
            preds = torch.argmax(logits, dim=-1)
            allpreds.append(preds[0])
            alllabels.append(labels[0])

# Once all predictions are done, move lists to CPU
allpreds = [pred.item() for pred in allpreds]
alllabels = [label.item() for label in alllabels]

# Compute accuracy
accuracy = accuracy_score(alllabels, allpreds)
precision = precision_score(alllabels, allpreds, average='weighted')  # Considering class imbalance
recall = recall_score(alllabels, allpreds, average='weighted')  # Considering class imbalance
f1 = f1_score(alllabels, allpreds, average='weighted')  # Considering class imbalance

print('Accuracy:', accuracy)
print('Precision:', precision)
print('Recall:', recall)
print('F1 Score:', f1)

# Print classification report
report = classification_report(alllabels, allpreds)
print('Classification Report:')
print(report)

Predicting:   0%|          | 0/12796 [00:00<?, ?batch/s]
tokenizing: 1it [00:00, 96.64it/s]
Predicting:   0%|          | 1/12796 [00:00<2:30:40,  1.42batch/s]
tokenizing: 1it [00:00, 277.36it/s]
Predicting:   0%|          | 2/12796 [00:01<2:23:21,  1.49batch/s]
tokenizing: 1it [00:00, 238.42it/s]
Predicting:   0%|          | 3/12796 [00:02<2:21:34,  1.51batch/s]
tokenizing: 1it [00:00, 149.11it/s]
Predicting:   0%|          | 4/12796 [00:02<2:21:07,  1.51batch/s]
tokenizing: 1it [00:00, 140.88it/s]
Predicting:   0%|          | 5/12796 [00:03<2:21:18,  1.51batch/s]
tokenizing: 1it [00:00, 206.41it/s]
Predicting:   0%|          | 6/12796 [00:03<2:21:26,  1.51batch/s]
tokenizing: 1it [00:00, 164.36it/s]
Predicting:   0%|          | 7/12796 [00:04<2:23:29,  1.49batch/s]
tokenizing: 1it [00:00, 165.82it/s]
Predicting:   0%|          | 8/12796 [00:05<2:23:36,  1.48batch/s]
tokenizing: 1it [00:00, 106.57it/s]
Predicting:   0%|          | 9/12796 [00:06<2:24:39,  1.47batch/s]
tokenizing: 1it [

Skipping example 79 as the total token count 2481 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 128.04it/s]
Predicting:   1%|          | 81/12796 [00:54<1:56:58,  1.81batch/s]
tokenizing: 1it [00:00, 205.65it/s]
Predicting:   1%|          | 82/12796 [00:55<2:04:56,  1.70batch/s]
tokenizing: 1it [00:00, 200.49it/s]
Predicting:   1%|          | 83/12796 [00:55<2:11:09,  1.62batch/s]
tokenizing: 1it [00:00, 90.82it/s]
Predicting:   1%|          | 84/12796 [00:56<2:15:05,  1.57batch/s]
tokenizing: 1it [00:00, 58.07it/s]
Predicting:   1%|          | 85/12796 [00:57<2:20:24,  1.51batch/s]
tokenizing: 1it [00:00, 242.08it/s]
Predicting:   1%|          | 86/12796 [00:57<2:21:30,  1.50batch/s]
tokenizing: 1it [00:00, 103.74it/s]
Predicting:   1%|          | 87/12796 [00:58<2:22:44,  1.48batch/s]
tokenizing: 1it [00:00, 144.31it/s]
Predicting:   1%|          | 88/12796 [00:59<2:24:18,  1.47batch/s]
tokenizing: 1it [00:00, 156.50it/s]
Predicting:   1%|          | 89/12796 [00:59<2:24:18,  1.47batch/s]
tokenizing: 1it [00:00, 224.91it/s]
Predicting:   1%|          | 

Skipping example 96 as the total token count 4597 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 139.45it/s]
Predicting:   1%|          | 98/12796 [01:05<1:51:53,  1.89batch/s]
tokenizing: 1it [00:00, 110.43it/s]
Predicting:   1%|          | 99/12796 [01:05<1:59:18,  1.77batch/s]
tokenizing: 1it [00:00, 202.84it/s]
Predicting:   1%|          | 100/12796 [01:06<2:04:26,  1.70batch/s]
tokenizing: 1it [00:00, 241.47it/s]
Predicting:   1%|          | 101/12796 [01:07<2:08:24,  1.65batch/s]
tokenizing: 1it [00:00, 290.08it/s]
Predicting:   1%|          | 102/12796 [01:07<2:11:10,  1.61batch/s]
tokenizing: 1it [00:00, 271.32it/s]
Predicting:   1%|          | 103/12796 [01:08<2:13:23,  1.59batch/s]
tokenizing: 1it [00:00, 232.00it/s]
Predicting:   1%|          | 104/12796 [01:09<2:14:57,  1.57batch/s]
tokenizing: 1it [00:00, 274.73it/s]
Predicting:   1%|          | 105/12796 [01:09<2:16:11,  1.55batch/s]
tokenizing: 1it [00:00, 121.64it/s]
Predicting:   1%|          | 106/12796 [01:10<2:18:42,  1.52batch/s]
tokenizing: 1it [00:00, 128.65it/s]
Predicting:   1%|   

...

Skipping example 12672 as the total token count 3081 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 99.82it/s]
Predicting:  99%|█████████▉| 12674/12796 [2:21:18<01:04,  1.89batch/s]
tokenizing: 1it [00:00, 169.96it/s]
Predicting:  99%|█████████▉| 12675/12796 [2:21:19<01:07,  1.78batch/s]
tokenizing: 1it [00:00, 128.13it/s]
Predicting:  99%|█████████▉| 12676/12796 [2:21:19<01:10,  1.70batch/s]
tokenizing: 1it [00:00, 105.44it/s]
Predicting:  99%|█████████▉| 12677/12796 [2:21:20<01:13,  1.63batch/s]
tokenizing: 1it [00:00, 138.44it/s]
Predicting:  99%|█████████▉| 12678/12796 [2:21:21<01:14,  1.58batch/s]
tokenizing: 1it [00:00, 157.92it/s]
Predicting:  99%|█████████▉| 12679/12796 [2:21:21<01:16,  1.54batch/s]
tokenizing: 1it [00:00, 223.30it/s]
Predicting:  99%|█████████▉| 12680/12796 [2:21:22<01:16,  1.51batch/s]
tokenizing: 1it [00:00, 125.29it/s]
Predicting:  99%|█████████▉| 12681/12796 [2:21:23<01:16,  1.50batch/s]
tokenizing: 1it [00:00, 72.39it/s]
Predicting:  99%|█████████▉| 12682/12796 [2:21:23<01:17,  1.48batch/s]
tokenizing: 1it [00:00, 228.31it/s]
Pr

Skipping example 12754 as the total token count 6844 exceeds the maximum sequence length 2048.



tokenizing: 1it [00:00, 182.50it/s]
Predicting: 100%|█████████▉| 12756/12796 [2:22:13<00:21,  1.89batch/s]
tokenizing: 1it [00:00, 238.61it/s]
Predicting: 100%|█████████▉| 12757/12796 [2:22:13<00:21,  1.78batch/s]
tokenizing: 1it [00:00, 141.49it/s]
Predicting: 100%|█████████▉| 12758/12796 [2:22:14<00:22,  1.67batch/s]
tokenizing: 1it [00:00, 60.03it/s]
Predicting: 100%|█████████▉| 12759/12796 [2:22:15<00:23,  1.59batch/s]
tokenizing: 1it [00:00, 137.59it/s]
Predicting: 100%|█████████▉| 12760/12796 [2:22:15<00:23,  1.55batch/s]
tokenizing: 1it [00:00, 101.82it/s]
Predicting: 100%|█████████▉| 12761/12796 [2:22:16<00:22,  1.53batch/s]
tokenizing: 1it [00:00, 113.75it/s]
Predicting: 100%|█████████▉| 12762/12796 [2:22:17<00:22,  1.51batch/s]
tokenizing: 1it [00:00, 98.77it/s]
Predicting: 100%|█████████▉| 12763/12796 [2:22:17<00:22,  1.49batch/s]
tokenizing: 1it [00:00, 149.15it/s]
Predicting: 100%|█████████▉| 12764/12796 [2:22:18<00:21,  1.49batch/s]
tokenizing: 1it [00:00, 98.86it/s]
Pre

Accuracy: 0.8606879220983195
Precision: 0.9051363138564804
Recall: 0.8606879220983195
F1 Score: 0.8772144535986668
Classification Report:
              precision    recall  f1-score   support

           0       0.96      0.88      0.92     11493
           1       0.38      0.68      0.49      1241

    accuracy                           0.86     12734
   macro avg       0.67      0.78      0.70     12734
weighted avg       0.91      0.86      0.88     12734

